In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import pyarrow as pa
import pyarrow.parquet as pq
import statsmodels.api as sm
import scipy
from scipy.stats import norm
from scipy.stats.mstats import gmean

from statsmodels.nonparametric.smoothers_lowess import lowess

from numpy.lib.stride_tricks import sliding_window_view
import functions_mem as fm

from datetime import datetime
from pathlib import Path

# Load data

In [2]:
df = pd.read_parquet('/opt/storage/shared/aesop/aesop_shared/ensamble_modelling/aesop_2026_01_21_mun.parquet')

sea_key = pd.read_parquet('/opt/storage/shared/aesop/aesop_shared/ensamble_modelling/def_sea_MEM_out_27_01_2026.parquet')

In [3]:
lst = ['co_uf','nm_uf','nm_municipio','co_ibge', 'epiyear', 'epiweek','year_week', 'atend_totais', 'atend_ivas','ra_atend_ivas','ra_atend_ivas_ma',]

df = df[lst]

#  Get baselines and thresholds

In [12]:
lst_sea = [2022, 2023, 2024] #2020, 2021

results = []

for cod in df.co_ibge.unique():

    row = sea_key.loc[sea_key.co_ibge == cod].head(1)

    if row.empty:
        print(f"⚠️ No season/delta for {cod}")
        continue

    week_start_seas = int(
        row["season_def"]
        .str.extract(r"w(\d+)")
        .iloc[0, 0]
    )

    delta_used = row["delta_used"].iloc[0]

    set_muni = df[df.co_ibge == cod].copy()

    set_muni["atend_ivas_ma"] = (
        set_muni["atend_ivas"]
        .rolling(window=4, min_periods=1)
        .mean()
    )

    if week_start_seas == 0:
        col_year = "epiyear"
    else:
        set_muni = fm.add_sea(set_muni, n_week=week_start_seas)
        col_year = f"season_w{week_start_seas}"

    summary, details = fm.mem_epidemic_period(
        set_muni,
        col_year=col_year,
        col_series="atend_ivas_ma",
        delta=delta_used,
    )

 
    baseline,  post_baseline, epidemic_threshold, post_threshold, df_thresholds_intensity  = fm.baseline_thresholds(
    set_muni,
    summary,
    lst_sea=[2022, 2023, 2024],
    value_col="atend_ivas",
    col_year = col_year, #f'season_w{week_start_seas}',
    col_week="epiweek"
    )
    
    summary = summary.assign(co_ibge = cod,
                             week_start_seas = week_start_seas,
                             col_year_str = col_year,
                             baseline = baseline,
                             post_baseline = post_baseline,
                             epidemic_threshold = epidemic_threshold,
                             post_threshold = post_threshold,
                             low_level = df_thresholds_intensity.value.iloc[0],
                             medium_level = df_thresholds_intensity.value.iloc[1],
                             high_level = df_thresholds_intensity.value.iloc[2],
                            )
    
    results.append(summary)

/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_index

⚠️ No season/delta for 110003


/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:275: RuntimeWarning: invalid value encountered in divide
  p_j_r = t_j_r / tS
/usr/local/lib/python3.10/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy

⚠️ No season/delta for 110140


/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:275: RuntimeWarning: invalid value encountered in divide
  p_j_r = t_j_r / tS
/usr/local/lib/python3.10/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy

...

/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_index

⚠️ No season/delta for 520570


/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_index

⚠️ No season/delta for 520960


/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  season["id"] = range(1, len(season) + 1)
/home/juliane.oliveira/workspace/IDEA_model/tmp/functions_mem.py:444: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_index

In [13]:
final = pd.concat(results)

In [14]:
#final.to_parquet('/Users/julianeoliveira/Documents/Projects/AESOP/Artigo Classification/results/mem_output_29_09_25.parquet')

out_dir = Path("/opt/storage/shared/aesop/aesop_shared/ensamble_modelling")
#/Users/julianeoliveira/Downloads")

fname = f"mem_output_{datetime.now():%d_%m_%Y}.parquet"

final.to_parquet(out_dir / fname)

In [16]:
final.co_ibge.nunique()

5518

In [18]:
final

epiyear  r_j_estr  k_start  k_end  co_ibge  week_start_seas col_year_str  \
0      2017        27        2     28   110001               39   season_w39   
1      2018        13       35     47   110001               39   season_w39   
2      2019        15       36     50   110001               39   season_w39   
3      2020        12       41     52   110001               39   season_w39   
4      2021        18       17     34   110001               39   season_w39   
..      ...       ...      ...    ...      ...              ...          ...   
5      2022         8        2      9   530010               52   season_w52   
6      2023        11       13     23   530010               52   season_w52   
7      2024        14       11     24   530010               52   season_w52   
8      2025        20       14     33   530010               52   season_w52   
9      2026         4        1      4   530010               52   season_w52   

       baseline  post_baseline  epidemic_threshold  post_threshold  \
0     31.536585      25.116279           78.145816       54.850851   
1     31.536585      25.116279           78.145816       54.850851   
2     31.536585      25.116279           78.145816       54.850851   
3     31.536585      25.116279           78.145816       54.850851   
4     31.536585      25.116279           78.145816       54.850851   
..          ...            ...                 ...             ...   
5   9872.884615    9799.370000        20951.960082    27142.006942   
6   9872.884615    9799.370000        20951.960082    27142.006942   
7   9872.884615    9799.370000        20951.960082    27142.006942   
8   9872.884615    9799.370000        20951.960082    27142.006942   
9   9872.884615    9799.370000        20951.960082    27142.006942   

       low_level  medium_level    high_level  
0      60.284821    123.999309    152.128406  
1      60.284821    123.999309    152.128406  
2      60.284821    123.999309    152.128406  
3      60.284821    123.999309    152.128406  
4      60.284821    123.999309    152.128406  
..           ...           ...           ...  
5   17451.720149  27716.480832  31600.241525  
6   17451.720149  27716.480832  31600.241525  
7   17451.720149  27716.480832  31600.241525  
8   17451.720149  27716.480832  31600.241525  
9   17451.720149  27716.480832  31600.241525  

[55180 rows x 14 columns]